# Avaliação 02


Grupo 5:
*   Allane Oliveira
*   Pedro
*   Karolayne Belo
*   Samuel Morais
*   Vitor Rodrigues

#### Inicialização do Ambiente


In [43]:
# Instalar pacotes necessários e bibliotecas
!pip install networkx pyvis

import networkx as nx
from pyvis.network import Network
from IPython.display import display, HTML
import pandas as pd
import math
import matplotlib.pyplot as plt
import functools
import heapq

#### Criação dos grafos e vizualizações


In [3]:
def ler_grafo(caminho_arquivo):
    arestas = []
    with open(caminho_arquivo, "r") as file:
        linhas = [l.strip() for l in file if l.strip()]

    # O laço itera por cada linha, separando a origem e o destino das arestas e verifica se ambas as partes estão corretas, tanto a origem quanto o destino, e então retorna uma lista com as arestas.
    for linha in linhas[1:]:
        partes = [p.strip() for p in linha.split(',')]
        if len(partes) == 3:
            #Converte para inteiros
            origem = int(partes[0]) if partes[0].isdigit() else partes[0]
            destino = int(partes[1]) if partes[1].isdigit() else partes[1]
            peso = int(partes[2])
            arestas.append((origem, destino, peso))
        else:
            print(f"Erro na linha: {linha}")

    return arestas

class grafosBases:
    def __init__(self, arestas = None, caminho_digrafo = None, direcionado = None):
        self.direcionado = True if direcionado is None else direcionado
        if arestas:
            self.arestas = arestas
        else:
            self.arestas = ler_grafo(caminho_digrafo)

        self.vertices = []

        # Remove vértices duplicados e ordena
        vertices_ordenados = sorted({v for aresta in self.arestas for v in aresta[:-1]})

        # Se todos os vértices são números, ordena numericamente
        if all(str(v).isdigit() for v in vertices_ordenados):
            self.vertices = sorted([int(v) for v in vertices_ordenados])
        else:
            self.vertices = sorted(vertices_ordenados)

        # Dicionario que relaciona o indice do vertice na matriz de adj com o vertice
        self.indices_dos_vertices = {v : i for i, v in enumerate(self.vertices)}
        # Dicionario que relaciona a label do vertice com o indice do vert na matriz de adj
        self.labels_dos_vertices = {i : v for i, v in enumerate(self.vertices)}

        # Cria matriz de adjacência
        n = len(self.vertices)
        self.matriz = [[math.inf] * n for _ in range(n)]
        for origem, destino, peso in self.arestas:
            i = self.indices_dos_vertices[origem]
            j = self.indices_dos_vertices[destino]
            self.matriz[i][j] = peso
            if not self.direcionado:
                self.matriz[j][i] = peso
        # return grafo

    def criar_digrafo(self, arestas):
        self.arestas = arestas

        self.vertices = []

        # Remove vértices duplicados e ordena
        vertices_ordenados = sorted({v for aresta in arestas for v in aresta[:-1]})

        # Se todos os vértices são números, ordena numericamente
        if all(str(v).isdigit() for v in vertices_ordenados):
            self.vertices = sorted([int(v) for v in vertices_ordenados])
        else:
            self.vertices = sorted(vertices_ordenados)

        # Dicionario que relaciona o indice do vertice na matriz de adj com o vertice
        self.indices_dos_vertices = {v : i for i, v in enumerate(self.vertices)}
        # Dicionario que relaciona a label do vertice com o indice do vert na matriz de adj
        self.labels_dos_vertices = {i : v for i, v in enumerate(self.vertices)}

        # Cria matriz de adjacência
        n = len(self.vertices)
        self.matriz = [[math.inf] * n for _ in range(n)]
        for origem, destino, peso in self.arestas:
            i = self.indices_dos_vertices[origem]
            j = self.indices_dos_vertices[destino]
            self.matriz[i][j] = peso
            if not self.direcionado:
                self.matriz[j][i] = peso
        # return grafo




Esta função permite selecionar arestas e vértices, possibilitando visualizar tanto as arestas associadas a cada vértice quanto os vértices ligados a uma aresta específica. Além disso, o processo é interativo, facilitando a exploração do grafo.


In [18]:
def grafo_pyvis(grafo, cor_no = "#b892ff", cor_font = "#2E0854", pesos_visizu=True):
  # Escolhe o tipo de grafo do NetworkX
  G = nx.DiGraph() if grafo.direcionado else nx.Graph()

  # Adiciona os vértices ao grafo do NetworkX
  G.add_nodes_from(grafo.vertices)

  # Adiciona as arestas com seus pesos
  for origem, destino, peso in grafo.arestas:
    G.add_edge(origem, destino, weight=peso)

  # Cria o objeto Pyvis para visualização
  net = Network(notebook=True, font_color=cor_font, directed=grafo.direcionado, cdn_resources="in_line", width="100%", height="450px")

  # Adiciona os nós ao Pyvis
  for n in G.nodes:
    net.add_node(n, color=cor_no, size=15, label= str(n))

  # Adiciona as arestas ao Pyvis
  for u,v,d in G.edges(data = True):
    if pesos_visizu is True:
      title = str(d.get('weight', ''))
      net.add_edge(u, v, label=title, width=1.5, color="#c9a98d")
    else:
      net.add_edge(u, v, width=1.5, color="#c9a98d")

  # Ajusta afastamento entre os nós
  net.repulsion(spring_length=100)

  # Gera e exibe o HTML do grafo
  display(HTML(net.generate_html()))

  return G

In [40]:
digrafo1 = grafosBases(caminho_digrafo="./data/digrafo1.csv", direcionado=False)
digrafo1_2 = grafosBases(caminho_digrafo="./data/digrafo1.csv", direcionado=True)
digrafo2 = grafosBases(caminho_digrafo="./data/digrafo2.csv", direcionado=True)
digrafo3 = grafosBases(caminho_digrafo="./data/digrafo3.csv", direcionado=True)
grafo1 = grafosBases(caminho_digrafo="./data/grafo1.csv", direcionado=False)

## ÁRVORES GERADORAS MÍNIMAS
Uma árvore geradora mínima é uma árvore geradora no qual tem o menor custo em relação as outras, em um grafo ponderado(ARESTAS) G.

In [20]:
G = grafo_pyvis(digrafo1, pesos_visizu=True, cor_font="#ed80a0", cor_no="#ed80a0")

### 1. Algoritmo de Kruskal





O código implementa o algoritmo de Kruskal: percorre a matriz de adjacência para coletar as arestas, ordena por peso e usa Union-Find para adicionar arestas sem formar ciclos, retornando a Árvore Geradora Mínima com n−1 arestas.
#### O que deve ser feito no algoritmo:
1. Listar todas as arestas com seus pesos.
2. Ordenar as arestas por peso crescente.
3. Inicializar cada vértice como componente separado (Union-Find).
4. Percorrer as arestas em ordem e em caso de ciclo ignora a aresta.
5. Parar em n-1 arestas.


#### Entrada Esperada:
Grafo gerado a partir de um arquivo .csv

#### Saída Esperada:
Lista de arestas da AGM e seu peso total.
A corretude pode ser verificada comparando com o resultado do NetworkX.

In [28]:
kruskal = list(nx.minimum_spanning_edges(G, algorithm="kruskal"))
arestas_formatadas = [(i[0],i[1],i[2]['weight']) for i in kruskal]
print("Árvore Geradora Esperada:", arestas_formatadas)
peso_total_esperado = sum(data["weight"] for _,_, data in kruskal)
print(f"Peso total esperado da AGM: {peso_total_esperado}")


Árvore Geradora Esperada: [(6, 11, 0), (1, 11, 1), (2, 3, 1), (7, 12, 1), (9, 14, 1), (12, 17, 1), (14, 15, 1), (1, 2, 2), (3, 4, 2), (3, 9, 2), (6, 7, 2), (9, 18, 2), (11, 16, 2), (4, 5, 4), (13, 18, 4), (5, 10, 5), (17, 19, 5), (8, 9, 7)]
Peso total esperado da AGM: 43


#### Nosso algoritmo:

In [29]:
def kruskal(grafo):
    # lista de arestas em (u, v, peso)
    arestas = []

    # vai pecorrer a matriz de adjacência do grafo p coletar todas as arestas (evitando repetir)
    for i, linha in enumerate(grafo.matriz):
        for j, peso in enumerate(linha):
            if i < j and peso != math.inf:
                origem = grafo.labels_dos_vertices[i]
                destino = grafo.labels_dos_vertices[j]
                # so para add
                arestas.append((origem, destino, peso))

    # ordenacao por peso, do menor para o maior
    arestas.sort(key=lambda x: x[2])
    print(f"Arestas ordenadas: {arestas}")
    # estrutura onion find > melhor para evita ciclos
    pai = {} #pai de cd elemento
    rank = {}

  # cria conjunto de cd elemento
    def make_set(v):
        pai[v] = v
        rank[v] = 0

  # encontra raiz
    def find(v):
        if pai[v] != v:
            pai[v] = find(pai[v])
        return pai[v]

  # junta os os conjuntos
    def union(a, b):
        ra, rb = find(a), find(b)
        if ra != rb:
            if rank[ra] < rank[rb]:
                pai[ra] = rb
            elif rank[ra] > rank[rb]:
                pai[rb] = ra
            else:
                pai[rb] = ra
                rank[ra] += 1

    # inicializa os conjuntos
    for v in grafo.vertices:
        make_set(v)

    # arestas da árvore
    t = []

    for u, v, peso in arestas:
        if find(u) != find(v):
            union(u, v)
            t.append((u, v, peso))

  # retorna apenas as arestas da avore
    return grafosBases(t, direcionado=False)

alg_kruskal = kruskal(digrafo1)

G_kruskal = grafo_pyvis(alg_kruskal, pesos_visizu=True,cor_font="#e97d71", cor_no="#e97d71")

print("ÁRVORE GERADORA ALGORITMO:", alg_kruskal.arestas)
peso_total_visto = sum([aresta[2] for aresta in alg_kruskal.arestas])
print(f"Peso total da AGM gerada por nosso algoritmo: {peso_total_visto}")

Arestas ordenadas: [(6, 11, 0), (1, 11, 1), (2, 3, 1), (7, 12, 1), (9, 14, 1), (12, 17, 1), (14, 15, 1), (1, 2, 2), (3, 4, 2), (3, 9, 2), (6, 7, 2), (9, 18, 2), (11, 16, 2), (1, 6, 3), (12, 16, 3), (4, 5, 4), (11, 12, 4), (13, 18, 4), (5, 10, 5), (7, 13, 5), (17, 19, 5), (10, 14, 6), (2, 6, 7), (4, 10, 7), (8, 9, 7), (7, 8, 8), (3, 6, 9), (4, 9, 9), (10, 15, 9), (3, 8, 10), (4, 13, 15), (14, 19, 18), (17, 18, 20)]


ÁRVORE GERADORA ALGORITMO: [(6, 11, 0), (1, 11, 1), (2, 3, 1), (7, 12, 1), (9, 14, 1), (12, 17, 1), (14, 15, 1), (1, 2, 2), (3, 4, 2), (3, 9, 2), (6, 7, 2), (9, 18, 2), (11, 16, 2), (4, 5, 4), (13, 18, 4), (5, 10, 5), (17, 19, 5), (8, 9, 7)]
Peso total da AGM gerada por nosso algoritmo: 43


### 2. Algoritmo de Prim

O código implementa o algoritmo de Prim, iniciando a Árvore Geradora Mínima (AGM) a partir de um vértice escolhido. A partir desse vértice inicial, o algoritmo expande a árvore selecionando sempre a aresta de menor peso que conecta um vértice já incluído na árvore a um vértice ainda não visitado.

#### O que deve ser feito no algoritmo:
1. Escolher um vértice inicial e adicioná-lo à árvore (conjunto Z).
2. Listar todos os vértices restantes no conjunto N.
3. Procurar entre as arestas que saem de Z aquela com menor peso que conecta a um vértice de N.
4. Adicionar essa aresta à AGM e mover o novo vértice de N para Z.
5. Repetir o processo até que todos os vértices estejam na árvore.

#### Entrada esperada:
Um grafo lido a partir de um arquivo .csv contendo as arestas e seus pesos.

#### Saída esperada:
A lista de arestas que compõem a AGM, junto com a soma total dos pesos.
É possível verificar a corretude comparando com a implementação do NetworkX (nx.minimum_spanning_edges).


In [33]:
prim= list(nx.minimum_spanning_edges(G, algorithm="prim"))
print("ÁRVORE GERADORA ESPERADA:", [(i[0],i[1],i[2]['weight']) for i in prim])
peso_total_esperado = sum(aresta[2] for aresta in [(i[0],i[1],i[2]['weight']) for i in prim])
print(f"Peso total esperado da AGM: {peso_total_esperado}")

ÁRVORE GERADORA ESPERADA: [(1, 11, 1), (11, 6, 0), (1, 2, 2), (2, 3, 1), (11, 16, 2), (6, 7, 2), (7, 12, 1), (12, 17, 1), (3, 4, 2), (3, 9, 2), (9, 14, 1), (14, 15, 1), (9, 18, 2), (4, 5, 4), (18, 13, 4), (17, 19, 5), (5, 10, 5), (9, 8, 7)]
Peso total esperado da AGM: 43


#### Nosso algoritmo:

In [57]:
def prim(grafo, inicial):
    # Conjunto vertices incluidos na arvore (inicializado apenas com o vertice inicial)
    z = set([grafo.indices_dos_vertices[inicial]])
    # Conjunto de vertices nao pertencentes a arvore.
    n = set(list(map(lambda vertice : grafo.indices_dos_vertices[vertice], grafo.vertices)))
    n.remove(grafo.indices_dos_vertices[inicial])

    # Conjunto de arestas integrando a arvore
    t = []

    # Funcao para achar a aresta minima de vertices de 'z' para vertices de 'n'
    def obter_aresta_minima(grafo, vertices_processados : set):
        # Pega a linha referente ao vertice atual na matriz
        # inicialia o peso minimo com infinito
        peso_min = math.inf
        vertice_origem_selecionado = None
        vertice_destino_selecionado = None
        for idx_linha in vertices_processados:
            for i, peso in enumerate(grafo.matriz[idx_linha]):
                if i in vertices_processados: # Se o vertice ja esta no conjunto z, continua
                    continue
                if peso < peso_min:
                    vertice_origem_selecionado = idx_linha
                    vertice_destino_selecionado = i
                    peso_min = peso
        return (vertice_origem_selecionado, vertice_destino_selecionado, peso_min)

    while len(n) > 0:
        # Obtem a aresta de menor custo com relacao aos vertices incluidos em Z
        aresta_selecionada = obter_aresta_minima(grafo, z)
        # Atualiza os conjuntos para incluir o vertice incidente em Z e remove-lo de N, alem de incluir a aresta selecionada em T
        n.remove(aresta_selecionada[1]) # O(1)
        z.add(aresta_selecionada[1]) # O(1)
        t.append((grafo.labels_dos_vertices[aresta_selecionada[0]], grafo.labels_dos_vertices[aresta_selecionada[1]], aresta_selecionada[2]))

    return grafosBases(t, direcionado=False) # Retorna digrafo da arvore minimagrafo1 = grafosBases(caminho_digrafo="./data/digrafo1.csv", direcionado=False)

alg_prim = prim(digrafo1, 1)

G_prim = grafo_pyvis(alg_prim, pesos_visizu=True, cor_font="#e97d71", cor_no="#e97d71")

print("ÁRVORE GERADORA ALGORITMO:", alg_prim.arestas)
peso_total_visto = sum([aresta[2] for aresta in alg_prim.arestas])
print(f"Peso total da AGM gerada por nosso algoritmo: {peso_total_visto}")

ÁRVORE GERADORA ALGORITMO: [(1, 11, 1), (11, 6, 0), (1, 2, 2), (2, 3, 1), (3, 4, 2), (3, 9, 2), (9, 14, 1), (14, 15, 1), (6, 7, 2), (7, 12, 1), (12, 17, 1), (9, 18, 2), (11, 16, 2), (4, 5, 4), (18, 13, 4), (5, 10, 5), (17, 19, 5), (9, 8, 7)]
Peso total da AGM gerada por nosso algoritmo: 43


## CAMINHO MAIS CURTO
É o menor caminho existente, em relação a custo, entre os nós v e w de um grafo ponderado G.

In [42]:
D = grafo_pyvis(digrafo1_2, pesos_visizu=True, cor_font="#68a03b", cor_no="#68a03b")

### 5. Algoritmo de Dijkstra

O código implementa o algoritmo de Dijkstra para encontrar o caminho mínimo a partir de um vértice inicial até todos os demais vértices do grafo. Ele utiliza uma fila de prioridade (heap) para escolher sempre o próximo vértice com a menor distância acumulada, garantindo eficiência no processo.

As distâncias são armazenadas em um dicionário, e os predecessores registram o vértice anterior no caminho mínimo, permitindo reconstruir o caminho ao final.

#### O que deve se fazer:
1. Inicializar todas as distâncias com inf, exceto o vértice inicial (0).
2. Inserir o vértice inicial na fila de prioridade.
3. Repetir até a fila esvaziar:
*   Remover o vértice com a menor distância registrada.
*   Para cada vizinho, calcular a nova distância possível.
*   Se for menor que a conhecida, atualizar a distância e o predecessor.
*   Inserir o vizinho atualizado na fila.
4.  Ao final, as distâncias mínimas e os predecessores representarão o caminho mínimo.

#### Entrada esperada
Um grafo direcionado lido de arquivo .csv contendo arestas e pesos.
Um vértice inicial escolhido pelo usuário.

#### Saída esperada

Um dicionário com as menores distâncias desde o vértice inicial e um dicionário de predecessores, indicando o caminho mínimo.

A saída pode ser validada usando a implementação do NetworkX.


In [65]:
# Distâncias e predecessores (NetworkX)
pred_nx, dist_nx = nx.dijkstra_predecessor_and_distance(D, source=1)
target = 15
print("\n=== DIJKSTRA (NETWORKX) ===")

print("\n→ Distância mínima de 1 até 15:")
if target in dist_nx:
    print(dist_nx[target])
else:
    print("Não existe caminho entre 1 e 15.")

print("\n→ Caminho mínimo de 1 até 15:")
try:
    caminho_1_15 = nx.dijkstra_path(D, source=1, target=target)
    print(caminho_1_15)
except nx.NetworkXNoPath:
    print("Não existe caminho entre 1 e 15.")


=== DIJKSTRA (NETWORKX) ===

→ Distância mínima de 1 até 15:
20

→ Caminho mínimo de 1 até 15:
[1, 11, 6, 7, 8, 9, 14, 15]


#### Nosso algoritmo

In [47]:
def dijkstra(grafo, inicial):
    distancias = {v: math.inf for v in grafo.vertices}
    predecessores = {v: None for v in grafo.vertices}

    vistos = {}
    pq = []

    distancias[inicial] = 0
    inicio_idx = grafo.indices_dos_vertices[inicial]
    heapq.heappush(pq, (0, inicio_idx))

    while pq:
        dist_u, u_idx = heapq.heappop(pq)

        if u_idx in vistos and dist_u > vistos[u_idx]:
            continue

        vistos[u_idx] = dist_u
        u_label = grafo.labels_dos_vertices[u_idx]

        for v_idx, peso in enumerate(grafo.matriz[u_idx]):

            if peso == math.inf:
                continue

            v_label = grafo.labels_dos_vertices[v_idx]

            nova_dist = dist_u + peso

            if nova_dist < distancias[v_label]:
                distancias[v_label] = nova_dist
                predecessores[v_label] = u_label
                heapq.heappush(pq, (nova_dist, v_idx))

    return distancias, predecessores


def reconstruindo_caminho(predecessores, origem, destino):
    caminho = []
    vertice_atual = destino
    while vertice_atual is not None:
        caminho.append(vertice_atual)
        vertice_atual = predecessores[vertice_atual]
    caminho.reverse()
    return caminho


In [56]:
digrafo1 = grafosBases(caminho_digrafo="./data/digrafo1.csv", direcionado=True)
G_nx = grafo_pyvis(digrafo1, direcionado=True, pesos_visizu=True)

vertice_inicial = 1
distancias_impl, predecessores_impl = dijkstra(digrafo1, vertice_inicial)

#Executa o algoritmo de Dijkstra implementado
print("--- DIJKSTRA (IMPLEMENTADO) ---")
print("===== Distâncias =====")
print(dict(sorted(distancias_impl.items())))
print("===== Predecessores =====")
print(dict(sorted(predecessores_impl.items())))


# Executa o algoritmo de Dijkstra do Networkx
print("\n--- DIJKSTRA (NETWORKX) ---")

pred_nx, dist_nx = nx.dijkstra_predecessor_and_distance(G_nx, source=vertice_inicial)
pred_nx[vertice_inicial] = None


print("===== Distâncias =====")
print(dict(sorted(dist_nx.items())))
print("===== Predecessores =====")
print(dict(sorted(pred_nx.items())))

# D_dijkstra = grafo_pyvis(dijkstra, direcionado=False, pesos_visizu=True, cor_font="#fb9936", cor_no="#fb9936")
# print("CAMINHO MINIMO ESPERADO:", list(nx.dijkstra_path(D_dijkstra)))
# print("CAMINHO MINIMO ALGORITMO:", dijkstra)


--- DIJKSTRA (IMPLEMENTADO) ---
===== Distâncias =====
{1: 0, 2: 2, 3: 3, 4: 5, 5: 9, 6: 1, 7: 3, 8: 11, 9: 5, 10: 12, 11: 1, 12: 4, 13: 8, 14: 6, 15: 7, 16: 3, 17: 5, 18: 7, 19: 10}

 ===== Predecessores =====
{1: None, 2: 1, 3: 2, 4: 3, 5: 4, 6: 11, 7: 6, 8: 7, 9: 3, 10: 4, 11: 1, 12: 7, 13: 7, 14: 9, 15: 14, 16: 11, 17: 12, 18: 9, 19: 17}

 ===== Caminhos mínimos =====
Caminho mínimo (implementado) de 1 até 15: [1, 2, 3, 9, 14, 15]
--- DIJKSTRA (IMPLEMENTADO) ---
===== Distâncias =====
{1: 0, 2: 2, 3: 3, 4: 5, 5: 9, 6: 1, 7: 3, 8: 11, 9: 5, 10: 12, 11: 1, 12: 4, 13: 8, 14: 6, 15: 7, 16: 3, 17: 5, 18: 7, 19: 10}
===== Predecessores =====
{1: None, 2: 1, 3: 2, 4: 3, 5: 4, 6: 11, 7: 6, 8: 7, 9: 3, 10: 4, 11: 1, 12: 7, 13: 7, 14: 9, 15: 14, 16: 11, 17: 12, 18: 9, 19: 17}
===== Caminhos mínimos =====
Caminho mínimo de 1 para 1: [1]
Caminho mínimo de 1 para 2: [1, 2]
Caminho mínimo de 1 para 3: [1, 2, 3]
Caminho mínimo de 1 para 4: [1, 2, 3, 4]
Caminho mínimo de 1 para 5: [1, 2, 3, 4, 5]


### 6. Algoritmo de Bellman-Ford

Explicação do algoritmo:

Explicação do Código:

Entrada e Saída esperada:

In [ ]:
from os import wait
def bellman_ford(grafo, inicial):
  predecessores = {} # Dicionário {vertice : predecessor}
  distancias = {} # Dicionário {vertice : distância}
  arestas_arvore = [] # Arestas da arvóre de menor custo

  # Setando predecessores nulos e distancias infinitas
  for vertice in grafo.vertices:
    predecessores[vertice] = []
    distancias[vertice] = math.inf
  distancias[inicial] = 0 # Distancia do vertice inicial é zero

  for i in range(1, len(grafo.vertices) - 1):
    for u, v, w in grafo.arestas: # aresta (u, v), w = peso de (u,v)
      if distancias[v] > distancias[u] + w:
        distancias[v] = distancias[u] + w
        predecessores[v] = [u]

  # Checando ciclos negativos
  for u, v, w in grafo.arestas:
    if distancias[v] > distancias[u] + w:
      return False

  ## Gerando arvore de menores caminhos
  ##for u, v, w in grafo.arestas:
    ##if distancias[v] == distancias[u] + w:
      ##arestas_arvore.append((u,v,w))

  # Imprimindo distâncias e predecessores
  print("BELLMAN-FORD (IMPLEMENTADO):")
  print("===== Distâncias =====")
  print(f"{distancias}")
  print("===== Predecesssores =====")
  print(f"{predecessores}")

  return True

grafo1 = grafosBases(caminho_digrafo="./data/digrafo1.csv", direcionado=True)
G_NX = grafo_pyvis(grafo1, direcionado=True, pesos_visizu=True, cor_font="#fb9936", cor_no="#fb9936")

if bellman_ford(grafo1, 1):
  pred, dist = nx.bellman_ford_predecessor_and_distance(G_NX, source=1)

  print("BELLMAN-FORD (NETWORKX)")
  print("===== Distâncias =====")
  print(dict(sorted(dist.items())))
  print("===== Predecessores =====")
  print(dict(sorted(pred.items())))


BELLMAN-FORD (IMPLEMENTADO):
===== Distâncias =====
{1: 0, 2: 11, 3: 10, 4: 12, 5: 24, 6: 1, 7: 3, 8: 11, 9: 18, 10: 19, 11: 1, 12: 4, 13: 27, 14: 19, 15: 20, 16: 3, 17: 5, 18: 31, 19: 10}
===== Predecesssores =====
{1: [], 2: [3], 3: [6], 4: [3], 5: [10], 6: [11], 7: [6], 8: [7], 9: [8], 10: [4], 11: [1], 12: [7], 13: [4], 14: [9], 15: [14], 16: [11], 17: [12], 18: [13], 19: [17]}
BELLMAN-FORD (NETWORKX)
===== Distâncias =====
{1: 0, 2: 11, 3: 10, 4: 12, 5: 24, 6: 1, 7: 3, 8: 11, 9: 18, 10: 19, 11: 1, 12: 4, 13: 27, 14: 19, 15: 20, 16: 3, 17: 5, 18: 31, 19: 10}
===== Predecessores =====
{1: [], 2: [3], 3: [6], 4: [3], 5: [10], 6: [11], 7: [6], 8: [7], 9: [8], 10: [4], 11: [1], 12: [7], 13: [4], 14: [9], 15: [14], 16: [11], 17: [12], 18: [13], 19: [17]}


### 7. Algoritmo de Floyd-Warshall, inclusive a Recuperação de Caminhos através da árvore de caminhos mais curtos

Explicação do algoritmo:

Explicação do Código:

Entrada e Saída esperada:

In [ ]:

def floyd_warshall(digrafo):
    predecessores = {i : [] for i in range(0, len(digrafo.matriz))}
    distancias = {i : [] for i in range(0, len(digrafo.matriz))}

    for idx_vertice, linha in enumerate(digrafo.matriz):
        for idx_vizinho, peso_vizinho in enumerate(linha):
            if idx_vertice == idx_vizinho:
                distancias[idx_vertice].append(0)
                predecessores[idx_vertice].append(idx_vertice)
            else:
                distancias[idx_vertice].append(peso_vizinho)
                pred = None if peso_vizinho == math.inf else idx_vertice
                predecessores[idx_vertice].append(pred)

    for k in range(0, len(digrafo.matriz)):
        for i, linha in enumerate(digrafo.matriz):
            for j, peso_destino in enumerate(linha):
                if distancias[i][k] + distancias[k][j] < distancias[i][j]:
                    distancias[i][j] = distancias[i][k] + distancias[k][j]
                    predecessores[i][j] = predecessores[k][j]
    return {digrafo.labels_dos_vertices[idx]: lista for idx, lista in distancias.items()}, {digrafo.labels_dos_vertices[idx]: [digrafo.labels_dos_vertices[j] if j is not None else None  for j in lista] for idx, lista in predecessores.items()}

def arvore_menor_custo(digrafo, raiz):
    distancias, predecessores = floyd_warshall(digrafo)
    distancias_raiz, predecessores_raiz = distancias[raiz], predecessores[raiz]
    arestas = []
    for idx, predecessor in enumerate(predecessores_raiz):
        label_destino = digrafo.labels_dos_vertices[idx]
        if predecessor:
            arestas.append((predecessor, label_destino, math.inf if distancias[predecessor][idx] is None else distancias[predecessor][idx]))
    return arestas

digrafo = grafosBases(caminho_digrafo=f"./data/digrafo1.csv", direcionado=True)
distancias, predecessores = floyd_warshall(digrafo)
print("** Distancias **")
print(distancias)
print("** Predecessores **")
print(predecessores)

print("** Arvore **")
print(arvore_menor_custo(digrafo, 1))


** Distancias **
{1: [0, 11, 10, 12, 24, 1, 3, 11, 18, 19, 1, 4, 27, 19, 20, 3, 5, 31, 10], 2: [2, 0, 8, 10, 22, 3, 5, 13, 19, 17, 3, 6, 25, 20, 21, 5, 7, 29, 12], 3: [3, 1, 0, 2, 14, 4, 6, 10, 11, 9, 4, 7, 17, 12, 13, 6, 8, 21, 13], 4: [14, 12, 11, 0, 12, 15, 17, 21, 9, 7, 15, 18, 15, 10, 11, 17, 19, 19, 24], 5: [18, 16, 15, 4, 0, 19, 21, 25, 13, 11, 19, 22, 19, 14, 15, 21, 23, 23, 28], 6: [12, 10, 9, 11, 23, 0, 2, 10, 17, 18, 7, 3, 26, 18, 19, 9, 4, 30, 9], 7: [17, 15, 14, 16, 28, 5, 0, 8, 15, 23, 5, 1, 31, 16, 17, 7, 2, 35, 7], 8: [12, 10, 9, 11, 23, 13, 15, 0, 7, 18, 13, 16, 26, 8, 9, 15, 17, 30, 22], 9: [5, 3, 2, 4, 16, 6, 8, 12, 0, 11, 6, 9, 19, 1, 2, 8, 10, 23, 15], 10: [23, 21, 20, 9, 5, 24, 26, 30, 18, 0, 24, 27, 24, 6, 7, 26, 28, 28, 24], 11: [12, 10, 9, 11, 23, 0, 2, 10, 17, 18, 0, 3, 26, 18, 19, 2, 4, 30, 9], 12: [16, 14, 13, 15, 27, 4, 6, 14, 21, 22, 4, 0, 30, 22, 23, 6, 1, 34, 6], 13: [11, 9, 8, 10, 22, 10, 5, 13, 6, 17, 10, 6, 0, 7, 8, 12, 7, 4, 12], 14: [inf, inf, inf, 

## GRAFOS EULERIANOS
Dizemos que um grafo é Euleriano se ele possui um caminho ou ciclo Euleriano, onde:


*   Caminho Euleriano: Percuso no qual deve passar por todas as arestas apenas 1 vez, sem precisar iniciar e findar no mesmo vértice.
*   Ciclo Euleriano: Percuso que inicia em v, percorre todas as arestas apenas 1 vez, e finaliza no mesmo v.



In [88]:
A_grafo = grafo_pyvis(grafo1, pesos_visizu=False, cor_font="#fb9936", cor_no="#fb9936")

In [70]:
A_digrafo = grafo_pyvis(digrafo3, pesos_visizu= False)

O código implementa o algoritmo de Hierholzer para encontrar um caminho Euleriano ou um ciclo Euleriano, ou seja, um percurso que utiliza todas as arestas do grafo exatamente uma vez. Onde ele percorre o grafo removendo as arestas à medida que são usadas, construindo o caminho final.

Nos grafos não direcionados, ele verifica se o grafo é Euleriano analisando o grau dos vértices; já nos direcionados, utiliza o grau de entrada e saída.
Depois dessa verificação, inicia o percurso a partir de um vértice adequado e segue removendo arestas enquanto avança. Quando um vértice não possui mais arestas disponíveis, ele é adicionado ao circuito final. Ao terminar, o caminho acumulado representa o ciclo ou caminho Euleriano.

#### O que deve se fazer:

1. Construir uma lista de adjacência para manipular as arestas.
2. Verificar se o grafo pode possuir caminho/ciclo Euleriano:
* Não direcionado: graus pares ou exatamente dois ímpares.
* Direcionado: diferenças entre graus de entrada e saída.
3. Definir o vértice inicial apropriado.
4. Repetir enquanto houver vértices na pilha:
* Avançar para o próximo vizinho enquanto existir aresta disponível.
* Remover a aresta utilizada.
* Quando um vértice não tiver mais arestas, adicioná-lo ao circuito final.
5. Inverter o circuito obtido, resultando no caminho ou ciclo Euleriano.

#### Entrada esperada
Um grafo direcionado ou não direcionado lido de arquivo .csv contendo os vértices e suas arestas.

#### Saída esperada
Uma lista com a sequência dos vértices formando o caminho/ciclo Euleriano e a indicação do tipo retornado (“caminho” ou “ciclo”).

O resultado pode ser validado comparando com as funções equivalentes do NetworkX.

In [73]:
if nx.is_eulerian(A_grafo):
    print("GRAFO NÃO DIRECIONADO")
    print("CICLO ESPERADO:", list(nx.eulerian_circuit(A_grafo)))
else:
    print("GRAFO NÃO DIRECIONADO")
    print("CAMINHO ESPERADO:", list(nx.eulerian_path(A_grafo)))

if nx.is_eulerian(A_digrafo):
    print("GRAFO DIRECIONADO")
    print("CICLO ESPERADO:", list(nx.eulerian_circuit(A_digrafo)))
else:
    print("GRAFO DIRECIONADO")
    print("CAMINHO ESPERADO:", list(nx.eulerian_path(A_digrafo)))

GRAFO NÃO DIRECIONADO
CICLO ESPERADO: [(1, 3), (3, 6), (6, 7), (7, 5), (5, 6), (6, 4), (4, 5), (5, 2), (2, 4), (4, 3), (3, 2), (2, 1)]
GRAFO DIRECIONADO
CAMINHO ESPERADO: [('E', 'A'), ('A', 'F'), ('F', 'E'), ('E', 'D'), ('D', 'B'), ('B', 'D'), ('D', 'C'), ('C', 'B'), ('B', 'A'), ('A', 'B')]


#### Nosso algoritmo

##### Grafos não direcionados

In [81]:
def hierholzer_nao_direcionado(grafo):
    n = len(grafo.vertices)

    # Cria lista de adjacência
    adj = [[] for _ in range(n)]
    for origem, destino, _ in grafo.arestas:
        i = grafo.indices_dos_vertices[origem]
        j = grafo.indices_dos_vertices[destino]
        adj[i].append(j)
        adj[j].append(i)

    # Calcula graus e identifica vértices ímpares
    grau = [len(adj[i]) for i in range(n)]
    impares = [i for i, g in enumerate(grau) if g % 2 == 1]

    # Se houver mais de 2 vértices ímpares, não existe caminho/ciclo Euleriano
    if len(impares) not in [0, 2]:
        print("O grafo NÃO possui ciclo nem caminho Euleriano (não direcionado).")
        return

    # Se houver 2 ímpares → caminho começa por um deles; senão → começa no 0
    inicio = impares[0] if len(impares) == 2 else 0

    # Pilha usada para exploração e lista para registrar o circuito final
    caminho_atual = [inicio]
    vertice_atual = inicio
    circuito = []

    while caminho_atual:
        # percorre o grafo removendo arestas até fechar o caminho
        if len(adj[vertice_atual]) > 0:  # há arestas saindo
            caminho_atual.append(vertice_atual)
            prox = adj[vertice_atual][-1]
            adj[vertice_atual].pop()
            adj[prox].remove(vertice_atual)
            vertice_atual = prox
        else:  # sem arestas, fixa no circuito
            circuito.append(vertice_atual)
            vertice_atual = caminho_atual.pop()

    # inverte para ficar na ordem da caminhada
    circuito = circuito[::-1]

    # Determina se a sequência é ciclo ou caminho Euleriano
    tipo = "ciclo" if circuito[0] == circuito[-1] else "caminho"

    # Converte índices para nomes/labels originais do grafo
    L = [grafo.labels_dos_vertices[v] for v in circuito]

    return L, tipo

In [85]:
print("----- CICLO OU CAMINHO EULERIANO(GRAFOS) -----")
print(hierholzer_nao_direcionado(grafo1))

----- CICLO OU CAMINHO EULERIANO(GRAFOS) -----
([1, 3, 6, 7, 5, 6, 4, 5, 2, 4, 3, 2, 1], 'ciclo')


##### Grafos Direcionados

In [86]:
def hierholzer_direcionado(grafo):
    n = len(grafo.vertices)

    # Cria lista de adjacência
    adj = [[] for _ in range(n)]
    for origem, destino, _ in grafo.arestas:
        i = grafo.indices_dos_vertices[origem]
        j = grafo.indices_dos_vertices[destino]
        adj[i].append(j)

    # Calcula grau de entrada e de saída para cada vértice
    grau_entrada = [0] * n
    grau_saida = [0] * n
    for i in range(n):
        grau_saida[i] = len(adj[i])
        for j in adj[i]:
            grau_entrada[j] += 1

    # Verifica condições para existir caminho/ciclo Euleriano:
    #   - No máximo 1 vértice com saída = entrada + 1  (início)
    candidatos_inicio = [i for i in range(n) if grau_saida[i] - grau_entrada[i] == 1]

    #   - No máximo 1 vértice com entrada = saída + 1  (fim)
    candidatos_fim = [i for i in range(n) if grau_entrada[i] - grau_saida[i] == 1]

    if len(candidatos_inicio) > 1 or len(candidatos_fim) > 1:
        print("O grafo NÃO possui ciclo nem caminho Euleriano (direcionado).")
        return

    # Define ponto inicial, se houver algum candidato usa ele, se não começa do 0
    inicio = candidatos_inicio[0] if candidatos_inicio else 0

   # Contador de quantas arestas ainda restam para cada vértice
    cont_arestas = {i: len(adj[i]) for i in range(n)}
    caminho_atual = [inicio]  # pilha para simular o percurso
    vertice_atual = inicio  # vértice atual
    circuito = []  # circuito final

    # Algoritmo de Hierholzer:
    while caminho_atual:
        if cont_arestas[vertice_atual]:
            # Se ainda há arestas a percorrer, continua o caminho
            caminho_atual.append(vertice_atual)
            prox = adj[vertice_atual][-1]
            cont_arestas[vertice_atual] -= 1
            adj[vertice_atual].pop()
            vertice_atual = prox
        else:
            # Se não tem mais arestas, fecha o caminho
            circuito.append(vertice_atual)
            vertice_atual = caminho_atual.pop()

    # inverte para ficar na ordem da caminhada
    circuito = circuito[::-1]

    # Determina se a sequência é ciclo ou caminho Euleriano
    tipo = "ciclo" if circuito[0] == circuito[-1] else "caminho"

    # Converte índices para nomes/labels originais do grafo
    L = [grafo.labels_dos_vertices[v] for v in circuito]

    return L, tipo

In [87]:
print("----- CICLO OU CAMINHO EULERIANO(DIGRAFOS) -----")
print(hierholzer_direcionado(digrafo3))

----- CICLO OU CAMINHO EULERIANO(DIGRAFOS) -----
(['E', 'D', 'B', 'D', 'C', 'B', 'A', 'F', 'E', 'A', 'B'], 'caminho')
